In [1]:
import numpy as np
import xarray as xr
import matplotlib as mpl
#mpl.use('Agg') # Must be before importing matplotlib.pyplot or pylab!
import matplotlib.pyplot as plt
import matplotlib.ticker as ticker

import pandas as pd
import os
#import seaborn as sns
import timeit
#start_time = timeit.default_timer()
from datetime import datetime,timedelta
from dask.diagnostics import ProgressBar
from functools import partial

In [2]:
ProgressBar().register()

In [3]:
# #%% plot parameters
# mpl.rcParams['axes.linewidth'] = 2.0 #set the value globally
# plt.rc('font', family='serif',size = 18)  # controls default text layout
# plt.rc('axes', titlesize=18)     # fontsize of the axes title
# plt.rc('axes', labelsize=18)    # fontsize of the x and y labels
# plt.rc('xtick', labelsize=18)    # fontsize of the tick labels
# plt.rc('ytick', labelsize=18)    # fontsize of the tick labels
# plt.rc('legend', fontsize=18)    # legend fontsize
# plt.rc('figure', titlesize=18)  # fontsize of the figure title

# #sns.set()

# plt.rc('text', usetex=False)


In [4]:
def _subset_process_time(ds,var,iop):
    
    #subset for the variable(s)
    ds = ds[var]
    ds['time'] = ds.time.dt.round('T')
    #IOP02
    if iop=='iop02': ds['time'] = pd.to_datetime('2019-08-22') + ds['time'].values
    #IOP03
    if iop=='iop03': ds['time'] = pd.to_datetime('2019-09-24') + ds['time'].values
    return(ds)

def _process_time(ds,iop):
    #round time to the nearest minute (30minute for PALM output)
    ds['time'] = ds.time.dt.round('T')
    #IOP02
    if iop=='iop02':ds['time'] = pd.to_datetime('2019-08-22') + ds['time'].values
    #IOP03
    if iop=='iop03':ds['time'] = pd.to_datetime('2019-09-24') + ds['time'].values    
    return(ds)

#function to concatenate all files for an ensemble member and if needed read in all ensemble members
def open_concat_member_files(ensemble_numbers,file,iop):
    data_list = []
    #loop through ensemble members
    if np.size(ensemble_numbers) > 1:
        for member_num in ensemble_numbers:    

            start_time = timeit.default_timer()
            if iop=='iop02': source_folder = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP2/ensemble.member.'+str(member_num) 
            #file = 'DATA_3D_AV_NETCDF_N02slice' 

            #Make a folder list and read in all the files from those folders. 
            folder_list = os.listdir(source_folder) 
            folder_list.sort() 
            file_list = [] 
            for folder in folder_list: 
                file_list.append(source_folder + '/' +folder+'/'+file) 
            file_list.sort()
            print(folder_list)

            #combine all the data along the time dimenstion 
            #don't combine them sequentially, but infer the sequence from coordinate values 
            #do this in parallel 
            #pull in only those values with a time dimension 
            var = ['w','theta','q','wtheta','wq']
            partial_func = partial(_subset_process_time, var=var,iop=iop)
            ds = xr.open_mfdataset(file_list,preprocess=partial_func) 
            ds.close() 
            print('Member',str(member_num),'finished collecting data')    
            #subset for time and day and collect into another list
            #for day1
            data_list.append(ds)
            elapsed = timeit.default_timer() - start_time
            print('Done with member',str(member_num),' Time elapsed ',elapsed, 'seconds')
        return(data_list)
            
    else:
        member_num =ensemble_numbers

        #loop through ensemble members
        start_time = timeit.default_timer()
        #IOP02
        if iop=='iop02':source_folder = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP2/ensemble.member.'+str(member_num) 
        #IOP03
        if iop=='iop03':source_folder = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP03/OUTPUT/ensemble.member.'+str(member_num) 
        
        #file = 'DATA_3D_AV_NETCDF_N03slice' 
        #file = 'DATA_1D_PR_NETCDF_N02slice' 

        #Make a folder list and read in all the files from those folders. 
        folder_list = os.listdir(source_folder) 
        folder_list.sort() 
        file_list = [] 
        for folder in folder_list: 
            file_list.append(source_folder + '/' +folder+'/'+file) 
        file_list.sort()
        print(folder_list)
        
        #combine all the data along the time dimenstion 
        partial_func = partial(_process_time,iop=iop)    
        ds = xr.open_mfdataset(file_list,preprocess=partial_func) 
        ds.close() 
        print('Member',str(member_num),'finished collecting data')    
        #subset for time and day and collect into another list
        #for day1
        #data_list.append(ds)
        elapsed = timeit.default_timer() - start_time
        print('Done with member',str(member_num),' Time elapsed ',elapsed, 'seconds')
        return(ds)

def calculate_turb_flux(ds):
    #subset for the variable(s)
    ds['theta_interpolated'] = ds.theta.rename({'zu_3d': 'zw_3d'}).interp_like(ds.w)
    ds['q_interpolated'] = ds.q.rename({'zu_3d': 'zw_3d'}).interp_like(ds.w)

    ds['wtheta_turb'] = ds['wtheta'] - ds.w*ds.theta_interpolated
    ds['wq_turb'] = ds['wq'] - ds.w*ds.q_interpolated


    ds['wtheta_turb_energy'] = ds['wtheta_turb']*1.17*1005
    ds['wq_turb_energy'] = ds['wq_turb']*1.17*1000*2501

    return ds


In [5]:
def _subset_process_time_hom(ds,var,iop):    
    #subset for the variable(s)
    ds = ds[var]
    ds['time'] = ds.time.dt.round('T')
    #IOP02
    if iop=='iop02': ds['time'] = pd.to_datetime('2019-08-22 22:00') + ds['time'].values
    #IOP03
    if iop=='iop03': ds['time'] = pd.to_datetime('2019-09-24') + ds['time'].values
    return(ds)

def _process_time_hom(ds,iop):
    #round time to the nearest minute (30minute for PALM output)
    ds['time'] = ds.time.dt.round('T')
    #IOP02
    if iop=='iop02':ds['time'] = pd.to_datetime('2019-08-22 22:00') + ds['time'].values
    #IOP03
    if iop=='iop03':ds['time'] = pd.to_datetime('2019-09-24') + ds['time'].values    
    return(ds)

In [6]:
#function to concatenate all files for an ensemble member and if needed read in all ensemble members
def open_concat_member_files_hom(ensemble_numbers,file,iop):
    data_list = []
    #loop through ensemble members
    if np.size(ensemble_numbers) > 1:
        for member_num in ensemble_numbers:    

            start_time = timeit.default_timer()
            if iop=='iop02': source_folder = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP2_parent_child1_hom/ensemble.member.'+str(member_num) 
            #file = 'DATA_3D_AV_NETCDF_N02slice' 

            #Make a folder list and read in all the files from those folders. 
            folder_list = os.listdir(source_folder) 
            folder_list.sort() 
            file_list = [] 
            for folder in folder_list: 
                file_list.append(source_folder + '/' +folder+'/'+file) 
            file_list.sort()
            print(folder_list)

            #combine all the data along the time dimenstion 
            #don't combine them sequentially, but infer the sequence from coordinate values 
            #do this in parallel 
            #pull in only those values with a time dimension 
            var = ['w','theta','q','wtheta','wq']
            partial_func = partial(_subset_process_time_hom, var=var,iop=iop)
            ds = xr.open_mfdataset(file_list,preprocess=partial_func) 
            ds.close()
            #check if the time index has only unique values 
            u, c = np.unique(ds.time.values, return_counts=True)
            #if not, keep the second, latest value for the ds
            if np.sum(c > 1) > 0 : ds = ds.drop_duplicates(dim='time', keep='last')

            print('Member',str(member_num),'finished collecting data')
            
            #subset for time and day and collect into another list
            #for day1
            data_list.append(ds)
            elapsed = timeit.default_timer() - start_time
            print('Done with member',str(member_num),' Time elapsed ',elapsed, 'seconds')
        return(data_list)
            
    else:
        member_num =ensemble_numbers

        #loop through ensemble members
        start_time = timeit.default_timer()
        #IOP02
        if iop=='iop02':source_folder = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP2/ensemble.member.'+str(member_num) 
        #IOP03
        if iop=='iop03':source_folder = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP03/OUTPUT/ensemble.member.'+str(member_num) 
        
        #file = 'DATA_3D_AV_NETCDF_N03slice' 
        #file = 'DATA_1D_PR_NETCDF_N02slice' 

        #Make a folder list and read in all the files from those folders. 
        folder_list = os.listdir(source_folder) 
        folder_list.sort() 
        file_list = [] 
        for folder in folder_list: 
            file_list.append(source_folder + '/' +folder+'/'+file) 
        file_list.sort()
        print(folder_list)
        
        #combine all the data along the time dimenstion 
        partial_func = partial(_process_time,iop=iop)    
        ds = xr.open_mfdataset(file_list,preprocess=partial_func) 
        ds.close() 
        print('Member',str(member_num),'finished collecting data')    
        #subset for time and day and collect into another list
        #for day1
        #data_list.append(ds)
        elapsed = timeit.default_timer() - start_time
        print('Done with member',str(member_num),' Time elapsed ',elapsed, 'seconds')
        return(ds)

#### IOP02

Checkout the normalized profile plots for daytime dispersive fluxes and ensemble mean fluxes

In [ ]:
#for IOP02, I ran 7 simulations till 1400 and one has data till 1330. 
#I will plot profiles for 1200 and 1400 or 1330. 
#see how they look and then maybe rerun the one simulation for one or two more hours. 


In [ ]:
#I need boundary layer heights and surface fluxes from 1100 to 1400.
# to normalise the flux profiles

In [5]:
file = 'DATA_3D_AV_NETCDF_N02slice' 
iop = 'iop02'
member_list = np.arange(1,9)
file_list = [] 

for member_num in member_list:
    
    if iop=='iop02': source_folder = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP2_parent_child1_hom/ensemble.member.'+str(member_num) 
    #Make a folder list and read in all the files from those folders. 
    folder_list = os.listdir(source_folder) 
    folder_list.sort() 
    for folder in folder_list: 
        file_list.append(source_folder + '/' +folder+'/'+file) 
    file_list.sort()
    print(folder_list)

['01.ches_IOP2_parent_child1_hom1.29566']
['01.ches_IOP2_parent_child1_hom.22675']
['01.ches_IOP2_parent_child1_hom3.9492']
['01.ches_IOP2_parent_child1_hom4.20276']
['01.ches_IOP2_parent_child1_hom5.26111']
['01.ches_IOP2_parent_child1_hom6.20862']
['01.ches_IOP2_parent_child1_hom7.1842']
['01. ches_IOP2_parent_child1_hom8.32767']


In [6]:
file_list

['/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP2_parent_child1_hom/ensemble.member.1/01.ches_IOP2_parent_child1_hom1.29566/DATA_3D_AV_NETCDF_N02slice',
 '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP2_parent_child1_hom/ensemble.member.2/01.ches_IOP2_parent_child1_hom.22675/DATA_3D_AV_NETCDF_N02slice',
 '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP2_parent_child1_hom/ensemble.member.3/01.ches_IOP2_parent_child1_hom3.9492/DATA_3D_AV_NETCDF_N02slice',
 '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP2_parent_child1_hom/ensemble.member.4/01.ches_IOP2_parent_child1_hom4.20276/DATA_3D_AV_NETCDF_N02slice',
 '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP2_parent_child1_hom/ensemble.member.5/01.ches_IOP2_parent_child1_hom5.26111/DATA_3D_AV_NETCDF_N02slice',
 '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP2_parent_child1_hom/ensemble.member.6/01.ches_IOP2_parent_child1_hom6.20862/DATA_3D_AV_NETCDF_N02slice',
 '/bog/incoming/cheesehead/palm/realistic_

In [13]:
data_list = []

#combine all the data along the time dimenstion 
#don't combine them sequentially, but infer the sequence from coordinate values 
#do this in parallel 
#pull in only those values with a time dimension 
for i, file in enumerate (file_list):
    var = ['w','theta','q','wtheta','wq']
    partial_func = partial(_subset_process_time_hom, var=var,iop=iop)
    ds = xr.open_dataset(file)
    ds.close() 
    ds = _subset_process_time_hom(ds,var,iop)
    #ds = ds.sel(time=slice('2019-09-24T11:00:00.000000000','2019-09-24T12:30:00.000000000')).resample(time='30T').mean()
    ds = ds.sel(time=slice('2019-08-23T11:30:00.000000000','2019-08-23T13:00:00.000000000'))
    ds = ds.expand_dims({'ensemble':1})
    print('Member finished collecting data')    
    #subset for time and day and collect into another list
    #for day1
    data_list.append(ds)
    

Member finished collecting data
Member finished collecting data
Member finished collecting data
Member finished collecting data
Member finished collecting data
Member finished collecting data
Member finished collecting data
Member finished collecting data


In [15]:
#add a new dimension, ensemble, to each member dataset


In [ ]:
check_ds = xr.concat(data_list[0:3],dim='ensemble')

In [ ]:
check_ds

In [ ]:
#add a new dimension, ensemble, to each member dataset
ds.expand_dims({'ensemble':1})
#set that value = member number

#create a dummy ensemble ds with only 2 members
xr.concat(data_list[0:2],dim='ensemble')

#update that datset with the other members


In [ ]:
xr.concat(data_list[0:5],dim='ensemble')

In [ ]:
data_list

In [ ]:
ensemble_member_ds_2_N02_iop02 = open_concat_member_files(2,'DATA_3D_AV_NETCDF_N02slice','iop02')


In [ ]:
zi_theta_av_list = []

IOP02_time_array = ensemble_ds_iop02_N02_hom.sel(member=1).time.values

vertical_slice = 2000
for i, time_step in enumerate(IOP02_time_array):
    zi_xy_av = (ensemble_ds_iop02_N02_hom.sel(member=1).sel(time = time_step,zu_3d=slice(10,vertical_slice)).theta.differentiate(coord = 'zu_3d', edge_order=1, datetime_unit=None).idxmax(dim='zu_3d')).mean('x').mean('y').compute()
    zi_theta_av_list.append(zi_xy_av)



In [ ]:
#open and read in surface flux values from the profile data
source_path = '/bog/incoming/cheesehead/palm/realistic_runs/ches_IOP2_parent_child1_hom/ensemble.member.1/01.ches_IOP2_parent_child1_hom1.29566/'
ensemble_member_1_profile_iop02_N02_hom = xr.open_dataset(source_path+'DATA_1D_PR_NETCDF_N02slice')
ensemble_member_1_profile_iop02_N02_hom.close()
ensemble_member_1_profile_iop02_N02_hom = _process_time_hom(ensemble_member_1_profile_iop02_N02_hom,'iop03')



Check the new function to combine data

In [7]:
member_list_iop02 = np.arange(1,9)
file = 'DATA_3D_AV_NETCDF_N02slice' 
iop = 'iop02'

ds_list = open_concat_member_files_hom(member_list_iop02,file,iop)

['01.ches_IOP2_parent_child1_hom1.29566', '02. ches_IOP2_parent_child1_hom1.9162']
Member 1 finished collecting data
Done with member 1  Time elapsed  0.07513901218771935 seconds
['01.ches_IOP2_parent_child1_hom.22675', '02.ches_IOP2_parent_child1_hom.4647']
Member 2 finished collecting data
Done with member 2  Time elapsed  0.06397778540849686 seconds
['01.ches_IOP2_parent_child1_hom3.9492', '02.ches_IOP2_parent_child1_hom3.14926']
Member 3 finished collecting data
Done with member 3  Time elapsed  0.06584605574607849 seconds
['01.ches_IOP2_parent_child1_hom4.20276', '02.ches_IOP2_parent_child1_hom4.808']
Member 4 finished collecting data
Done with member 4  Time elapsed  0.06450951099395752 seconds
['0.ches_IOP2_parent_child1_hom5.19920', '01.ches_IOP2_parent_child1_hom5.26111', '02.ches_IOP2_parent_child1_hom5.21747']


UFuncTypeError: ufunc 'add' cannot use operands with types dtype('O') and dtype('<M8[ns]')

In [54]:
ds_list

[<xarray.Dataset>
 Dimensions:  (time: 11, zw_3d: 250, y: 1008, x: 900, zu_3d: 250)
 Coordinates:
   * x        (x) float64 15.0 45.0 75.0 105.0 ... 2.692e+04 2.696e+04 2.698e+04
   * y        (y) float64 15.0 45.0 75.0 105.0 ... 3.016e+04 3.02e+04 3.022e+04
   * time     (time) datetime64[ns] 2019-08-23T11:00:00 ... 2019-08-23T16:00:00
   * zu_3d    (zu_3d) float64 0.0 6.0 18.0 30.0 ... 2.958e+03 2.97e+03 2.982e+03
   * zw_3d    (zw_3d) float64 0.0 12.0 24.0 ... 2.964e+03 2.976e+03 2.988e+03
 Data variables:
     w        (time, zw_3d, y, x) float32 dask.array<chunksize=(7, 250, 1008, 900), meta=np.ndarray>
     theta    (time, zu_3d, y, x) float32 dask.array<chunksize=(7, 250, 1008, 900), meta=np.ndarray>
     q        (time, zu_3d, y, x) float32 dask.array<chunksize=(7, 250, 1008, 900), meta=np.ndarray>
     wtheta   (time, zw_3d, y, x) float32 dask.array<chunksize=(7, 250, 1008, 900), meta=np.ndarray>
     wq       (time, zw_3d, y, x) float32 dask.array<chunksize=(7, 250, 1008, 900

In [51]:
ensemble_ds_iop02_N02_hom = xr.concat(ds_list,dim='ensemble')



/bog/spaleri/fen/miniconda3/envs/palm_analysis/lib/python3.10/site-packages/xarray/core/indexing.py:1228: PerformanceWarning: Slicing is producing a large chunk. To accept the large
chunk and silence this warning, set the option
    >>> with dask.config.set(**{'array.slicing.split_large_chunks': False}):
    ...     array[indexer]

To avoid creating the large chunks, set the option
    >>> with dask.config.set(**{'array.slicing.split_large_chunks': True}):
    ...     array[indexer]
  return self.array[key]
/bog/spaleri/fen/miniconda3/envs/palm_analysis/lib/python3.10/site-packages/xarray/core/indexing.py:1228: PerformanceWarning: Slicing is producing a large chunk. To accept the large
chunk and silence this warning, set the option
    >>> with dask.config.set(**{'array.slicing.split_large_chunks': False}):
    ...     array[indexer]

To avoid creating the large chunks, set the option
    >>> with dask.config.set(**{'array.slicing.split_large_chunks': True}):
    ...     array[indexer]